In [52]:
import pandas as pd
import pickle
import numpy as np
import matplotlib.pyplot as plt
from sklearn.mixture import GaussianMixture
from scipy import stats
import matplotlib.pyplot as plt
import sys
np.set_printoptions(threshold=sys.maxsize)

In [53]:
data2 = pd.read_pickle("preprocessed_data.pkl")

In [54]:
data = data2[['GPS_LAT', 'GPS_ALT', 'LandOwned', 'LandCultivated', 'LivestockHoldings', 'Food_Availability_kCal_MAE_day', 'Food_Self_Sufficiency_kCal_MAE_day',
'crop_sales_USD_PPP_pHH_Yr', 'value_crop_produce_USD_PPP_pHH_Yr', 'GHGEmissions']]

In [55]:
data

GPS_LAT  GPS_ALT  LandOwned  LandCultivated  LivestockHoldings  \
0        11.19   254.00       10.0             2.0               1.04   
1        11.19   346.00        NaN             1.2               4.00   
2        11.19   324.00        2.0             0.8               0.30   
3        11.19   326.00        NaN             0.8               5.43   
4        11.22   308.00       10.0             4.0               2.12   
...        ...      ...        ...             ...                ...   
35723   -13.82  1119.60        8.0             8.0               3.58   
35724   -13.82  1128.85        NaN            14.0               8.80   
35725   -13.82  1132.41        5.0             6.0               5.48   
35726   -13.82  1136.24        4.0             4.0               0.70   
35727   -13.82  1125.93        1.0             2.0               1.44   

       Food_Availability_kCal_MAE_day  Food_Self_Sufficiency_kCal_MAE_day  \
0                         4621.267353                          754.360895   
1                         2503.023263                         2303.522017   
2                          381.108158                          381.108158   
3                         9948.141738                          620.787518   
4                         2209.261281                         1767.543491   
...                               ...                                 ...   
35723                    21491.305517                        12770.090428   
35724                    11260.499490                         4217.809731   
35725                     4247.172555                         1221.939610   
35726                     5918.719620                         5918.719620   
35727                     4440.170043                         3999.475254   

       crop_sales_USD_PPP_pHH_Yr  value_crop_produce_USD_PPP_pHH_Yr  \
0                     164.857702                         242.318219   
1                       0.000000                         279.844923   
2                       0.000000                          23.278518   
3                     228.969031                         255.682085   
4                      22.896903                         184.734710   
...                          ...                                ...   
35723                2970.040440                        9187.374358   
35724                4501.379943                        8866.040295   
35725                1083.897904                        2007.669471   
35726                   0.000000                        2026.134892   
35727                 158.046197                        1843.270026   

       GHGEmissions  
0        702.949550  
1      94415.087935  
2        113.654565  
3      43062.200002  
4      13331.792068  
...             ...  
35723  34884.136689  
35724  79114.978038  
35725  46350.365405  
35726   7452.589981  
35727  13768.248392  

[35728 rows x 10 columns]

In [56]:
import impyute as impy
dir(impy)

['__all__',
 '__author__',
 '__build__',
 '__builtins__',
 '__cached__',
 '__copyright__',
 '__doc__',
 '__file__',
 '__license__',
 '__loader__',
 '__name__',
 '__package__',
 '__path__',
 '__spec__',
 '__title__',
 '__version__',
 'complete_case',
 'deletion',
 'em',
 'fast_knn',
 'imputation',
 'locf',
 'mean',
 'median',
 'mice',
 'mode',
 'moving_window',
 'random',
 'util']

In [57]:
d = data.to_numpy()

In [58]:
def nan_indices(data):
    """ Finds the indices of all missing values.
    Parameters
    ----------
    data: numpy.ndarray
    Returns
    -------
    List of tuples
        Indices of all missing values in tuple format; (i, j)
    """
    return np.argwhere(np.isnan(data))

In [59]:
nan_indices(d)

array([[    1,     2],
       [    3,     2],
       [   23,     2],
       [   24,     2],
       [   24,     3],
       [   29,     2],
       [   31,     2],
       [   34,     2],
       [   35,     2],
       [   36,     2],
       [   37,     2],
       [   38,     3],
       [   43,     2],
       [   48,     2],
       [   60,     2],
       [   63,     1],
       [   63,     2],
       [   64,     1],
       [   65,     1],
       [   65,     2],
       [   66,     1],
       [   66,     2],
       [   66,     3],
       [   67,     1],
       [   67,     2],
       [   68,     1],
       [   68,     2],
       [   69,     1],
       [   69,     2],
       [   69,     3],
       [   70,     1],
       [   71,     1],
       [   71,     2],
       [   72,     1],
       [   73,     1],
       [   74,     1],
       [   75,     1],
       [   76,     1],
       [   77,     1],
       [   78,     1],
       [   79,     1],
       [   80,     1],
       [   81,     1],
       [   

In [60]:
def em(data, loops=50):
    """ Imputes given data using expectation maximization.
    E-step: Calculates the expected complete data log likelihood ratio.
    M-step: Finds the parameters that maximize the log likelihood of the
    complete data.
    Parameters
    ----------
    data: numpy.nd.array
        Data to impute.
    loops: int
        Number of em iterations to run before breaking.
    inplace: boolean
        If True, operate on the numpy array reference
    Returns
    -------
    numpy.nd.array
        Imputed data.
    """
    nan_xy = nan_indices(data)
    for x_i, y_i in nan_xy:
        col = data[:, int(y_i)]
        mu = col[~np.isnan(col)].mean()
        std = col[~np.isnan(col)].std()
        col[x_i] = np.random.normal(loc=mu, scale=std)
        previous, i = 1, 1
        for i in range(loops):
            # Expectation
            mu = col[~np.isnan(col)].mean()
            std = col[~np.isnan(col)].std()
            # Maximization
            col[x_i] = np.random.normal(loc=mu, scale=std)
            # Break out of loop if likelihood doesn't change at least 10%
            # and has run at least 5 times
            delta = (col[x_i]-previous)/previous
            if i > 5 and delta < 0.1:
                data[x_i][y_i] = col[x_i]
                break
            data[x_i][y_i] = col[x_i]
            previous = col[x_i]
    return data

In [61]:
r = em(d)

In [62]:
r

array([[ 1.11900000e+01,  2.54000000e+02,  1.00000000e+01,
         2.00000000e+00,  1.04000000e+00,  4.62126735e+03,
         7.54360895e+02,  1.64857702e+02,  2.42318219e+02,
         7.02949550e+02],
       [ 1.11900000e+01,  3.46000000e+02,  1.07940546e+02,
         1.20000000e+00,  4.00000000e+00,  2.50302326e+03,
         2.30352202e+03,  0.00000000e+00,  2.79844923e+02,
         9.44150879e+04],
       [ 1.11900000e+01,  3.24000000e+02,  2.00000000e+00,
         8.00000000e-01,  3.00000000e-01,  3.81108158e+02,
         3.81108158e+02,  0.00000000e+00,  2.32785182e+01,
         1.13654565e+02],
       [ 1.11900000e+01,  3.26000000e+02,  7.87639355e+01,
         8.00000000e-01,  5.43000000e+00,  9.94814174e+03,
         6.20787518e+02,  2.28969031e+02,  2.55682085e+02,
         4.30622000e+04],
       [ 1.12200000e+01,  3.08000000e+02,  1.00000000e+01,
         4.00000000e+00,  2.12000000e+00,  2.20926128e+03,
         1.76754349e+03,  2.28969031e+01,  1.84734710e+02,
         1.

In [63]:
result = pd.DataFrame(r, columns=['GPS_LAT', 'GPS_ALT', 'LandOwned', 'LandCultivated', 'LivestockHoldings', 'Food_Availability_kCal_MAE_day', 'Food_Self_Sufficiency_kCal_MAE_day',
'crop_sales_USD_PPP_pHH_Yr', 'value_crop_produce_USD_PPP_pHH_Yr', 'GHGEmissions'])
result

GPS_LAT  GPS_ALT   LandOwned  LandCultivated  LivestockHoldings  \
0        11.19   254.00   10.000000             2.0               1.04   
1        11.19   346.00  107.940546             1.2               4.00   
2        11.19   324.00    2.000000             0.8               0.30   
3        11.19   326.00   78.763936             0.8               5.43   
4        11.22   308.00   10.000000             4.0               2.12   
...        ...      ...         ...             ...                ...   
35723   -13.82  1119.60    8.000000             8.0               3.58   
35724   -13.82  1128.85 -233.911818            14.0               8.80   
35725   -13.82  1132.41    5.000000             6.0               5.48   
35726   -13.82  1136.24    4.000000             4.0               0.70   
35727   -13.82  1125.93    1.000000             2.0               1.44   

       Food_Availability_kCal_MAE_day  Food_Self_Sufficiency_kCal_MAE_day  \
0                         4621.267353                          754.360895   
1                         2503.023263                         2303.522017   
2                          381.108158                          381.108158   
3                         9948.141738                          620.787518   
4                         2209.261281                         1767.543491   
...                               ...                                 ...   
35723                    21491.305517                        12770.090428   
35724                    11260.499490                         4217.809731   
35725                     4247.172555                         1221.939610   
35726                     5918.719620                         5918.719620   
35727                     4440.170043                         3999.475254   

       crop_sales_USD_PPP_pHH_Yr  value_crop_produce_USD_PPP_pHH_Yr  \
0                     164.857702                         242.318219   
1                       0.000000                         279.844923   
2                       0.000000                          23.278518   
3                     228.969031                         255.682085   
4                      22.896903                         184.734710   
...                          ...                                ...   
35723                2970.040440                        9187.374358   
35724                4501.379943                        8866.040295   
35725                1083.897904                        2007.669471   
35726                   0.000000                        2026.134892   
35727                 158.046197                        1843.270026   

       GHGEmissions  
0        702.949550  
1      94415.087935  
2        113.654565  
3      43062.200002  
4      13331.792068  
...             ...  
35723  34884.136689  
35724  79114.978038  
35725  46350.365405  
35726   7452.589981  
35727  13768.248392  

[35728 rows x 10 columns]

In [64]:
result.isnull().values.any()
result.isnull().sum().sum()

0

In [66]:
result.to_pickle('em_data.pkl')

In [67]:
dataa = pd.read_pickle("em.pkl")
dataa

FileNotFoundError: [Errno 2] No such file or directory: 'em.pkl'